In [1]:
import tensorflow as tf
import json
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error as mse
from sklearn.metrics import mean_absolute_error as mae

2023-06-25 22:20:02.635063: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-25 22:20:02.671267: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-25 22:20:02.672032: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-25 22:20:03.658377: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
file_path = '../dataset.json'

# Open the file and load its contents
with open(file_path, 'r') as json_file:
    # Read the file content
    file_content = json_file.read()

    # Split the content by newline to get individual JSON objects
    json_objects = file_content.split('\n')

data = []
# Process each JSON object
for json_object in json_objects:
    if json_object.strip() == '':
        continue  # Skip empty lines
    
    # Parse the JSON object
    data.append(json.loads(json_object))

print(len(data))

X = []
Y = []
Y_flat = []

for i in data:
    X.append(np.array(i['vector']))    
    Y.append(np.array(i['matrix']))
    
X_train, X_test, Y_train, Y_test = train_test_split(X,Y)
X_train = np.array(X_train)
X_test = np.array(X_test)
Y_train = np.array(Y_train)
Y_test = np.array(Y_test)
Y_train_flat =[i.flatten() for i in Y_train]
Y_test_flat =[i.flatten() for i in Y_test]
print(len(X_test))


1331
333


In [3]:
def get_metrics(y, p_y, model='model'):
    metrics = {}
    try:
        m = tf.keras.metrics.Accuracy(name="accuracy", dtype=None)
        m.update_state(y, p_y)
        metrics['accuracy'] = m.result().numpy()
    except:
        pass
    try:
        metrics['mse'] = mse(y,p_y)
    except:
        pass
    
    df = pd.DataFrame()
    
    print(len(y))
    m1 = [i.reshape(14,14) for i in y]
    m2 = [i.reshape(14,14) for i in p_y]
    
    for i in range(len(m1)):
        for j in range(len(m1[i])):
            # print(y[i], p_y[i])
            line = {"x":str(i),
                    "y":str(j),
                    "mse":str(mse(m1[i][j], m2[i][j])),
                    "mae":str(mae(m1[i][j],m2[i][j])),
                    }
            df = df.append(line,ignore_index=True)
            
    df.to_csv(f"{model}_test_results_by_component.csv")
    return metrics
    

# Handmade NN

In [4]:
# Define the neural network architecture
def build_crazy_model(input_dim, output_dim):
    model = tf.keras.models.Sequential([
        tf.keras.layers.Dense(128, activation='relu', input_shape=(input_dim,)),
        tf.keras.layers.Dense(256, activation='relu'),
        tf.keras.layers.Dense(512, activation='relu'),
        tf.keras.layers.Dense(1024, activation='relu'),
        tf.keras.layers.Dense(2048, activation='relu'),
        tf.keras.layers.Dense(4096, activation='relu'),
        tf.keras.layers.Dense(output_dim)
    ])
    return model
def build_model(input_dim, output_dim):
    model = tf.keras.models.Sequential([
        tf.keras.layers.Dense(256, activation='relu', input_shape=(input_dim,)),
        tf.keras.layers.Dense(512, activation='relu'),
        tf.keras.layers.Dense(512, activation='relu'),
        tf.keras.layers.Dense(512, activation='relu'),
        tf.keras.layers.Dense(1024, activation='relu'),
        tf.keras.layers.Dense(1024, activation='relu'),
        tf.keras.layers.Dense(1024, activation='relu'),
        tf.keras.layers.Dense(512, activation='relu'),
        tf.keras.layers.Dense(196)  # Output layer with shape (196,)
    ])
    return model

def build_model_recursive(input_dim, output_dim):
    model = tf.keras.models.Sequential([
        tf.keras.layers.Dense(256, activation='relu', input_shape=(input_dim,)),
        tf.keras.layers.Reshape((1, 256)),  # Reshape input to match LSTM requirements
        # tf.keras.layers.LSTM(512, return_sequences=True),
        tf.keras.layers.TimeDistributed(tf.keras.layers.Dense(256, activation='relu')),
        tf.keras.layers.LSTM(512),
        tf.keras.layers.Dense(output_dim)
    ])
    return model

# def build_model_convolutional(input_dim):
#     model = tf.keras.models.Sequential([
#         tf.keras.layers.Dense(256, activation='relu', input_shape=(input_dim,)),
#         tf.keras.layers.Dense(7*7*128, activation='relu'),
#         tf.keras.layers.Reshape((7, 7, 128)),
#         tf.keras.layers.Conv2DTranspose(32, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu'),
#         tf.keras.layers.Conv2DTranspose(2, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu'),
#         tf.keras.layers.Conv2D(1, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu'),
#         tf.keras.layers.Reshape((14, 14, 1))  # Update the output shape to (14, 14, 1)
#     ])
#     return model

In [5]:
# Define the input and output dimensions
input_dim = 128  # Dimensionality of the input vector
output_dim = 196  # Dimensionality of the output vector

In [6]:
# Build the model
model = build_model_recursive(input_dim, output_dim)
model_ann = build_model(input_dim, output_dim)
# model_conv = build_model_convolutional(input_dim)

# Compile the model
model.compile(optimizer='adam', loss='mse')
model_ann.compile(optimizer='adam', loss='mse')
model.summary()
model_ann.summary()
# model_conv.compile(optimizer='adam', loss='mse')

2023-06-25 22:20:05.221543: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:996] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2023-06-25 22:20:05.238248: W tensorflow/core/common_runtime/gpu/gpu_device.cc:1956] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 256)               33024     
                                                                 
 reshape (Reshape)           (None, 1, 256)            0         
                                                                 
 time_distributed (TimeDistr  (None, 1, 256)           65792     
 ibuted)                                                         
                                                                 
 lstm (LSTM)                 (None, 512)               1574912   
                                                                 
 dense_2 (Dense)             (None, 196)               100548    
                                                                 
Total params: 1,774,276
Trainable params: 1,774,276
Non-trainable params: 0
______________________________________________

2023-06-25 22:20:05.618891: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_2_grad/concat/split_2/split_dim' with dtype int32
	 [[{{node gradients/split_2_grad/concat/split_2/split_dim}}]]
2023-06-25 22:20:05.620318: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_grad/concat/split/split_dim' with dtype int32
	 [[{{node gradients/split_grad/concat/split/split_dim}}]]
2023-06-25 22:20:05.621582: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You mus

In [7]:
model_ann.fit(x=np.array(X_train),y=np.array(Y_train_flat), epochs=10)

Epoch 1/10
32/32 [==============================] - 2s 27ms/step - loss: 1008678.8750
Epoch 2/10
32/32 [==============================] - 1s 27ms/step - loss: 1325.6206
Epoch 3/10
32/32 [==============================] - 1s 27ms/step - loss: 1338.2740
Epoch 4/10
32/32 [==============================] - 1s 27ms/step - loss: 1381.9675
Epoch 5/10
32/32 [==============================] - 1s 27ms/step - loss: 1323.7711
Epoch 6/10
32/32 [==============================] - 1s 26ms/step - loss: 1323.7701
Epoch 7/10
32/32 [==============================] - 1s 26ms/step - loss: 1323.7692
Epoch 8/10
32/32 [==============================] - 1s 26ms/step - loss: 1323.7687
Epoch 9/10
32/32 [==============================] - 1s 26ms/step - loss: 1323.7673
Epoch 10/10
32/32 [==============================] - 1s 26ms/step - loss: 1323.7665


In [8]:
model.fit(x=np.array(X_train),y=np.array(Y_train_flat), epochs=10)

Epoch 1/10


2023-06-25 22:20:16.204845: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_2_grad/concat/split_2/split_dim' with dtype int32
	 [[{{node gradients/split_2_grad/concat/split_2/split_dim}}]]
2023-06-25 22:20:16.206845: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_grad/concat/split/split_dim' with dtype int32
	 [[{{node gradients/split_grad/concat/split/split_dim}}]]
2023-06-25 22:20:16.208633: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You mus

32/32 [==============================] - 3s 14ms/step - loss: 1323.6620
Epoch 2/10
32/32 [==============================] - 0s 14ms/step - loss: 1323.5497
Epoch 3/10
32/32 [==============================] - 0s 14ms/step - loss: 1323.4655
Epoch 4/10
32/32 [==============================] - 0s 14ms/step - loss: 1323.2805
Epoch 5/10
32/32 [==============================] - 0s 14ms/step - loss: 1323.1051
Epoch 6/10
32/32 [==============================] - 0s 14ms/step - loss: 1322.8988
Epoch 7/10
32/32 [==============================] - 0s 14ms/step - loss: 1322.7201
Epoch 8/10
32/32 [==============================] - 0s 14ms/step - loss: 1322.5419
Epoch 9/10
32/32 [==============================] - 0s 14ms/step - loss: 1322.3671
Epoch 10/10
32/32 [==============================] - 0s 13ms/step - loss: 1322.2303


In [9]:

Y_predicted = model.predict(np.array(X_test))
Y_ann_predicted = model_ann.predict(np.array(X_test))
# Y_conv_predicted = model_conv.predict(np.array(X_test))
print(get_metrics(Y_predicted, Y_test_flat, "rnn"))
print(get_metrics(Y_ann_predicted, Y_test_flat, "ann"))

11/11 [==============================] - 0s 3ms/step


2023-06-25 22:20:23.109975: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_2_grad/concat/split_2/split_dim' with dtype int32
	 [[{{node gradients/split_2_grad/concat/split_2/split_dim}}]]
2023-06-25 22:20:23.112000: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_grad/concat/split/split_dim' with dtype int32
	 [[{{node gradients/split_grad/concat/split/split_dim}}]]
2023-06-25 22:20:23.113518: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You mus

11/11 [==============================] - 0s 4ms/step
333


/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use

{'accuracy': 0.0, 'mse': 20.94289738762133}
333


/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use

{'accuracy': 0.0, 'mse': 21.330998790577027}


/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use

In [10]:
Y_predicted = [np.reshape(i, (14,14)) for i in Y_predicted]
# Y_predicted

In [11]:
Y_ann_predicted = [np.reshape(i, (14,14)) for i in Y_ann_predicted]
# Y_ann_predicted

# AutoKeras

In [12]:
import autokeras as ak
import numpy as np

In [13]:
# X_train = X_train.reshape(-1, 128)
# Y_train = Y_train.reshape(-1, 14,14)
train_set = tf.data.Dataset.from_tensor_slices((X_train, Y_train_flat))
test_set = tf.data.Dataset.from_tensor_slices((X_test, Y_test_flat))


In [14]:

input_node = ak.StructuredDataInput()
output_node = ak.StructuredDataBlock(categorical_encoding=True)(input_node)
output_node = ak.RegressionHead()(output_node)
reg = ak.AutoModel(
    inputs=input_node, outputs=output_node, overwrite=True, max_trials=5000
)
reg.fit(train_set,epochs=10, validation_split=0.15)
predicted_y = reg.predict(test_set)
# X_train = X_train.reshape(-1, 128)
# Y_train = Y_train.reshape(-1, 14,14)|
print(reg.evaluate(test_set))
print(get_metrics(Y_test, predicted_y,"auto_model"))

Trial 85 Complete [00h 00m 12s]
val_loss: 0.12752149999141693

Best val_loss So Far: 0.12017689645290375
Total elapsed time: 00h 15m 20s
INFO:tensorflow:Oracle triggered exit


2023-06-25 22:35:57.549745: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_27' with dtype double and shape [998,128]
	 [[{{node Placeholder/_27}}]]
2023-06-25 22:35:57.550474: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_69' with dtype double and shape [998,196]
	 [[{{node Placeholder/_69}}]]
2023-06-25 22:35:57.681754: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_27' with dtype double and 

Epoch 1/10


2023-06-25 22:36:02.702389: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_69' with dtype double and shape [998,196]
	 [[{{node Placeholder/_69}}]]
2023-06-25 22:36:02.703133: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_50' with dtype double and shape [998,196]
	 [[{{node Placeholder/_50}}]]


32/32 [==============================] - 3s 3ms/step - loss: 1324.0714 - mean_squared_error: 1324.0714
Epoch 2/10
32/32 [==============================] - 0s 3ms/step - loss: 1323.7322 - mean_squared_error: 1323.7322
Epoch 3/10
32/32 [==============================] - 0s 4ms/step - loss: 1323.2982 - mean_squared_error: 1323.2982
Epoch 4/10
32/32 [==============================] - 0s 4ms/step - loss: 1322.5361 - mean_squared_error: 1322.5361
Epoch 5/10
32/32 [==============================] - 0s 4ms/step - loss: 1321.8182 - mean_squared_error: 1321.8182
Epoch 6/10
32/32 [==============================] - 0s 4ms/step - loss: 1320.8226 - mean_squared_error: 1320.8226
Epoch 7/10
32/32 [==============================] - 0s 4ms/step - loss: 1321.4257 - mean_squared_error: 1321.4257
Epoch 8/10
32/32 [==============================] - 0s 4ms/step - loss: 1320.7611 - mean_squared_error: 1320.7611
Epoch 9/10
32/32 [==============================] - 0s 4ms/step - loss: 1319.7665 - mean_squared_er

...

2023-06-25 22:36:41.695856: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_28' with dtype double and shape [333,196]
	 [[{{node Placeholder/_28}}]]
2023-06-25 22:36:41.696230: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]


11/11 [==============================] - 1s 2ms/step - loss: 21.1218 - mean_squared_error: 21.1218
[21.121809005737305, 21.121809005737305]
333


/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use

{}


/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use

In [15]:
regressor = ak.StructuredDataRegressor(max_trials=150, overwrite=True)
regressor.fit(train_set, epochs=10, validation_split=0.15)
predicted_y = regressor.predict(test_set)
# X_train = X_train.reshape(-1, 128)
# Y_train = Y_train.reshape(-1, 14,14)
print(get_metrics(Y_test, predicted_y, "structured_regressor"))

print(regressor.evaluate(test_set))

Trial 104 Complete [00h 00m 10s]
val_loss: 0.22225496172904968

Best val_loss So Far: 0.11917945742607117
Total elapsed time: 00h 20m 22s
INFO:tensorflow:Oracle triggered exit


INFO:tensorflow:Oracle triggered exit
2023-06-25 22:57:14.557174: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype double and shape [998,196]
	 [[{{node Placeholder/_1}}]]
2023-06-25 22:57:14.558592: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_69' with dtype double and shape [998,196]
	 [[{{node Placeholder/_69}}]]
2023-06-25 22:57:14.699111: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Pla

Epoch 1/10


2023-06-25 22:57:19.961576: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_19' with dtype double and shape [998,128]
	 [[{{node Placeholder/_19}}]]
2023-06-25 22:57:19.962307: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_9' with dtype double and shape [998,196]
	 [[{{node Placeholder/_9}}]]


32/32 [==============================] - 3s 3ms/step - loss: 1324.0056 - mean_squared_error: 1324.0056
Epoch 2/10
32/32 [==============================] - 0s 3ms/step - loss: 1323.2316 - mean_squared_error: 1323.2316
Epoch 3/10
32/32 [==============================] - 0s 4ms/step - loss: 1322.7592 - mean_squared_error: 1322.7592
Epoch 4/10
32/32 [==============================] - 0s 4ms/step - loss: 1321.7621 - mean_squared_error: 1321.7621
Epoch 5/10
32/32 [==============================] - 0s 4ms/step - loss: 1320.1937 - mean_squared_error: 1320.1937
Epoch 6/10
32/32 [==============================] - 0s 4ms/step - loss: 1322.7357 - mean_squared_error: 1322.7357
Epoch 7/10
32/32 [==============================] - 0s 4ms/step - loss: 1321.8219 - mean_squared_error: 1321.8219
Epoch 8/10
32/32 [==============================] - 0s 4ms/step - loss: 1320.7045 - mean_squared_error: 1320.7045
Epoch 9/10
32/32 [==============================] - 0s 4ms/step - loss: 1319.6251 - mean_squared_er

...

11/11 [==============================] - 0s 3ms/step
333


/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(line,ignore_index=True)
/tmp/ipykernel_170212/877969581.py:28: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use

{}


2023-06-25 22:58:06.573200: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_20' with dtype double and shape [333,196]
	 [[{{node Placeholder/_20}}]]
2023-06-25 22:58:06.573589: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_19' with dtype double and shape [333,128]
	 [[{{node Placeholder/_19}}]]


11/11 [==============================] - 1s 2ms/step - loss: 21.1207 - mean_squared_error: 21.1207
[21.12065887451172, 21.12065887451172]


In [16]:
model = reg.export_model()
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 128)]             0         
                                                                 
 multi_category_encoding (Mu  (None, 128)              0         
 ltiCategoryEncoding)                                            
                                                                 
 normalization (Normalizatio  (None, 128)              257       
 n)                                                              
                                                                 
 dense (Dense)               (None, 32)                4128      
                                                                 
 batch_normalization (BatchN  (None, 32)               128       
 ormalization)                                                   
                                                             

In [17]:
model_regressor = regressor.export_model()
model_regressor.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 128)]             0         
                                                                 
 multi_category_encoding (Mu  (None, 128)              0         
 ltiCategoryEncoding)                                            
                                                                 
 normalization (Normalizatio  (None, 128)              257       
 n)                                                              
                                                                 
 dense (Dense)               (None, 16)                2064      
                                                                 
 batch_normalization (BatchN  (None, 16)               64        
 ormalization)                                                   
                                                             

In [18]:
import pandas as pd
X_test = X_test.reshape(-1, 128)
# Y = Y_test.reshape(-1, 128)
it = 0
for x in X_test:
    Y_ak_predicted =reg.predict(X_test)
    
df = pd.DataFrame(Y_ak_predicted)
df.to_csv("reg_output.csv")

2023-06-25 22:58:36.413049: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]
2023-06-25 22:58:36.413319: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]


11/11 [==============================] - 0s 2ms/step


2023-06-25 22:58:47.445283: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]
2023-06-25 22:58:47.445487: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]


11/11 [==============================] - 0s 2ms/step


2023-06-25 22:58:58.431592: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]
2023-06-25 22:58:58.431867: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]


...

11/11 [==============================] - 0s 2ms/step


2023-06-26 00:00:11.979972: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]
2023-06-26 00:00:11.980181: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]


11/11 [==============================] - 0s 2ms/step


2023-06-26 00:00:22.474676: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]
2023-06-26 00:00:22.474922: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [333,128]
	 [[{{node Placeholder/_0}}]]


11/11 [==============================] - 0s 2ms/step


In [19]:
# X_test = X_test.reshape(-1, 128)
# Y = Y_test.reshape(-1, 128)
it = 0
for x in X_test:
    Y_ak_predicted =regressor.predict(x)
    print(Y[it])

2023-06-26 00:00:33.418523: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [128]
	 [[{{node Placeholder/_0}}]]
2023-06-26 00:00:33.418796: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype double and shape [128]
	 [[{{node Placeholder/_0}}]]
2023-06-26 00:00:34.132389: I tensorflow/core/common_runtime/executor.cc:1197] [/job:localhost/replica:0/task:0/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: Determined shape must either match input shape along split_dim exa

InvalidArgumentError: Graph execution error:

Detected at node 'model/multi_category_encoding/split' defined at (most recent call last):
    File "<frozen runpy>", line 198, in _run_module_as_main
    File "<frozen runpy>", line 88, in _run_code
    File "/home/joramas/.pyenv/versions/3.11.2/lib/python3.11/site-packages/ipykernel_launcher.py", line 17, in <module>
      app.launch_new_instance()
    File "/home/joramas/.pyenv/versions/3.11.2/lib/python3.11/site-packages/traitlets/config/application.py", line 1043, in launch_instance
      app.start()
    File "/home/joramas/.pyenv/versions/3.11.2/lib/python3.11/site-packages/ipykernel/kernelapp.py", line 725, in start
      self.io_loop.start()
    File "/home/joramas/.pyenv/versions/3.11.2/lib/python3.11/site-packages/tornado/platform/asyncio.py", line 215, in start
      self.asyncio_loop.run_forever()
    File "/home/joramas/.pyenv/versions/3.11.2/lib/python3.11/asyncio/base_events.py", line 607, in run_forever
      self._run_once(

In [ ]:
pd.DataFrame(Y_test).to_csv("y_data")